In [3]:
from datasets import load_dataset

# dataset = load_dataset("dair-ai/emotion")
dataset = load_dataset("imsoumyaneel/sentiment-analysis-llama2")
dataset

Using custom data configuration imsoumyaneel--sentiment-analysis-llama2-406c8d12ee6e98f7


Extracting data files:   0%|          | 0/1 [00:00<?, ?it/s]

0 tables [00:00, ? tables/s]

/usr/local/lib/python3.9/dist-packages/datasets/download/streaming_download_manager.py:695: FutureWarning: the 'mangle_dupe_cols' keyword is deprecated and will be removed in a future version. Please take steps to stop the use of 'mangle_dupe_cols'
  return pd.read_csv(xopen(filepath_or_buffer, "rb", use_auth_token=use_auth_token), **kwargs)


Dataset csv downloaded and prepared to /root/.cache/huggingface/datasets/imsoumyaneel___csv/imsoumyaneel--sentiment-analysis-llama2-406c8d12ee6e98f7/0.0.0/652c3096f041ee27b04d2232d41f10547a8fecda3e284a79a0ec4053c916ef7a. Subsequent calls will reuse this data.


  0%|          | 0/1 [00:00<?, ?it/s]

DatasetDict({
    train: Dataset({
        features: ['sentence', 'label', 'text'],
        num_rows: 598298
    })
})

In [4]:
import pandas as pd

complete_dataset = dataset['train'].to_pandas()
complete_dataset['new_label'] = complete_dataset['label'].map({'joy': '0', 'neutral': '1', 'sadness': '2', 'anger': '3', 'fear': '4', 'love': '5', 'surprise': '6'}).values

train_dataset = complete_dataset.sample(frac=0.8,random_state=200)
test_dataset = complete_dataset.drop(train_dataset.index)

complete_dataset.info()
train_dataset.info()
test_dataset.info()

complete_dataset.head()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 598298 entries, 0 to 598297
Data columns (total 4 columns):
 #   Column     Non-Null Count   Dtype 
---  ------     --------------   ----- 
 0   sentence   598298 non-null  object
 1   label      598298 non-null  object
 2   text       598298 non-null  object
 3   new_label  598298 non-null  object
dtypes: object(4)
memory usage: 18.3+ MB
<class 'pandas.core.frame.DataFrame'>
Int64Index: 478638 entries, 352227 to 559736
Data columns (total 4 columns):
 #   Column     Non-Null Count   Dtype 
---  ------     --------------   ----- 
 0   sentence   478638 non-null  object
 1   label      478638 non-null  object
 2   text       478638 non-null  object
 3   new_label  478638 non-null  object
dtypes: object(4)
memory usage: 18.3+ MB
<class 'pandas.core.frame.DataFrame'>
Int64Index: 119660 entries, 0 to 598297
Data columns (total 4 columns):
 #   Column     Non-Null Count   Dtype 
---  ------     --------------   ----- 
 0   sentence   119660 

sentence    label  \
0                       I'll throw out the garbage .  neutral   
1  So Dick , how about getting some coffee for to...      joy   
2  Come on , you can at least try a little , besi...  neutral   
3  What ’ s wrong with that ? Cigarette is the th...    anger   
4                                Not for me , Dick .  neutral   

                                                text new_label  
0  ###Human:\nyou are a sentiment analist. guess ...         1  
1  ###Human:\nyou are a sentiment analist. guess ...         0  
2  ###Human:\nyou are a sentiment analist. guess ...         1  
3  ###Human:\nyou are a sentiment analist. guess ...         3  
4  ###Human:\nyou are a sentiment analist. guess ...         1

In [5]:
# imports for model creation
import tensorflow as tf
from keras import layers
from keras import losses
import keras
from tensorflow.keras.preprocessing.text import Tokenizer
from tensorflow.keras.preprocessing.sequence import pad_sequences

In [6]:
tokenizer = Tokenizer()
tokenizer.fit_on_texts(complete_dataset['sentence'])

vocab_size = len(tokenizer.word_index) + 1
max_length = 200    # max words in a sentence
embedding_dim = 50    # TODO: need to adjust accordinglys

X_train = tokenizer.texts_to_sequences(train_dataset['sentence'])
X_train = pad_sequences(X_train, maxlen=max_length, padding='post')

X_test = tokenizer.texts_to_sequences(test_dataset['sentence'])
X_test = pad_sequences(X_test, maxlen=max_length, padding='post')

y_train = train_dataset['new_label']
y_test = test_dataset['new_label']

from keras.utils import to_categorical

num_classes = 7  # Assuming you have 3 classes
y_train_encoded = to_categorical(y_train, num_classes=num_classes)
y_test_encoded = to_categorical(y_test, num_classes=num_classes)

In [7]:
labels = complete_dataset['label']

print(X_train.shape)
print(X_test.shape)
print(y_train.shape)
print(y_test.shape)

(478638, 200)
(119660, 200)
(478638,)
(119660,)


In [8]:
# Build the model
model = keras.Sequential([
  keras.layers.Embedding(input_dim=vocab_size, output_dim=embedding_dim, input_shape=(max_length,)),
  keras.layers.GlobalAveragePooling1D(),
  keras.layers.Dense(32, activation='relu'),
  keras.layers.Dense(7, activation='sigmoid')
])

In [9]:
# Compile the model
model.compile(loss='categorical_crossentropy', optimizer='adam', metrics=['accuracy'])

In [10]:
# split the dataset into train and test
# from sklearn.model_selection import train_test_split

# X_train, X_test, y_train, y_test = train_test_split(, labels, test_size=0.3, random_state=42, shuffle=True)
# X_train

In [12]:
# train the model
model.fit(X_train, y_train_encoded, epochs=10, batch_size=32, validation_data=(X_test, y_test_encoded))

Epoch 1/10
14958/14958 [==============================] - 55s 4ms/step - loss: 0.4894 - accuracy: 0.8447 - val_loss: 0.4174 - val_accuracy: 0.8586
Epoch 2/10
14958/14958 [==============================] - 54s 4ms/step - loss: 0.3798 - accuracy: 0.8692 - val_loss: 0.3835 - val_accuracy: 0.8651
Epoch 3/10
14958/14958 [==============================] - 54s 4ms/step - loss: 0.3453 - accuracy: 0.8761 - val_loss: 0.3638 - val_accuracy: 0.8655
Epoch 4/10
14958/14958 [==============================] - 54s 4ms/step - loss: 0.3166 - accuracy: 0.8810 - val_loss: 0.3513 - val_accuracy: 0.8645
Epoch 5/10
14958/14958 [==============================] - 55s 4ms/step - loss: 0.2941 - accuracy: 0.8848 - val_loss: 0.3548 - val_accuracy: 0.8669
Epoch 6/10
14958/14958 [==============================] - 54s 4ms/step - loss: 0.2789 - accuracy: 0.8881 - val_loss: 0.3423 - val_accuracy: 0.8654
Epoch 7/10
14958/14958 [==============================] - 55s 4ms/step - loss: 0.2675 - accuracy: 0.8909 - val_loss: 0

In [14]:
# Evaluate the model
loss, accuracy = model.evaluate(X_test, y_test_encoded)
accuracy

3740/3740 [==============================] - 6s 2ms/step - loss: 0.3639 - accuracy: 0.8604


0.8604295253753662

In [16]:
# save the model
import os
try:
    model.save("../models/sentimental-analysis-llama2.keras")
except FileNotFoundError:
    os.mkdir("../models")
    model.save("../models/sentimental-analysis-llama2.keras")

In [22]:
def preprocess_text(text):
    # Tokenize the text
    tokenized_text = tokenizer.texts_to_sequences([text])
    # Pad sequences to the same length as training data
    padded_text = pad_sequences(tokenized_text, maxlen=max_length, padding='post')
    return padded_text

# Preprocess the custom input text
preprocessed_text = preprocess_text("this is good")

# Make predictions
predictions = model.predict(preprocessed_text)

predictions

1/1 [==============================] - 0s 17ms/step


array([[0.809063  , 0.78246254, 0.02547726, 0.03657908, 0.00648503,
        0.02069169, 0.07264358]], dtype=float32)